In [1]:
import pandas as pd

It turns out [record 3082688](https://zenodo.org/records/3082688) is version 2 of [record 1247307](https://zenodo.org/records/1247307), where some mislabeling was fixed. Images from record 1247307 should not be used, so we will remove them here.

Will also add `hybrid_stat` and `file_url` columns so these can be explored with all functionality of the [data dashboard](https://huggingface.co./spaces/imageomics/dashboard-prototype).

In [2]:
df = pd.read_csv("../Jiggins_Zenodo_Img_Master.csv", low_memory=False)

In [3]:
df.nunique()

CAMID               12586
X                   49359
Image_name          37821
View                    7
zenodo_name            36
zenodo_link            32
Sequence            11301
Taxonomic_Name        363
Locality              645
Sample_accession     1571
Collected_by           12
Other_ID             3088
Date                  810
Dataset                 8
Store                 142
Brood                 226
Death_Date             82
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               6
file_type               3
record_number          32
species               246
subspecies            155
genus                  94
dtype: int64

In [4]:
df.record_number.info()

<class 'pandas.core.series.Series'>
RangeIndex: 49359 entries, 0 to 49358
Series name: record_number
Non-Null Count  Dtype
--------------  -----
49359 non-null  int64
dtypes: int64(1)
memory usage: 385.7 KB


In [5]:
df = df.loc[df.record_number != 1247307]
df.nunique()

CAMID               12586
X                   46439
Image_name          37821
View                    7
zenodo_name            35
zenodo_link            31
Sequence            11301
Taxonomic_Name        363
Locality              645
Sample_accession     1571
Collected_by           12
Other_ID             3088
Date                  810
Dataset                 8
Store                 142
Brood                 226
Death_Date             82
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               6
file_type               3
record_number          31
species               246
subspecies            155
genus                  94
dtype: int64

Checking all records on Zenodo for the [Butterfly Genetics Group](https://zenodo.org/communities/butterfly/records) (the overall source of the Jiggins data), [record 3477891](https://zenodo.org/records/3477891) and [record 2548678](https://zenodo.org/records/2548678) are marked as version 2 of records 3477412 & 1880783, respectively. Let's check that the first versions are not included.

It is also noted in [record 2548678](https://zenodo.org/records/2548678):
>Some images overlap with 'Cambridge butterfly wing collection batch 1', taken by Eva Whiltshire. Images here differ in having a white reflectance standard for calibration. Information on duplicates can be found in 'CAM.coll.patricio.batch2.csv'.

Note that this is a reference to [record 1247307](https://zenodo.org/records/1247307), so the overlap is in fact with Cambridge butterfly wing collection batch 1- version 2 ([record 3082688](https://zenodo.org/records/3082688)); it is unclear as yet if the duplication information will be acurate considering the mislabelings fixed between the versions.

In [6]:
v1s = [3477412, 1880783]
df.loc[df["record_number"].isin(v1s)].shape

(0, 26)

The good news is that neither of these earlier versions seem to have been picked up, so we can move on to assessing this and adding the `hybrid_stat` and `file_url` columns.

In [7]:
df.file_type.value_counts()

file_type
jpg    34152
raw    12226
tif       61
Name: count, dtype: int64

In [8]:
df.View.value_counts()

View
dorsal                22022
ventral               21704
forewing dorsal         406
hindwing dorsal         406
forewing ventral        406
hindwing ventral        406
dorsal and ventral       18
Name: count, dtype: int64

We have 31 unique records represented in the full dataset. When we reduce down to just the Heliconius images, this will probably be less.

### Add File URL Column

In [9]:
df["file_url"] = df["zenodo_link"] + "/files/" + df["Image_name"]
df.sample(4)

CAMID      X       Image_name     View  \
34925  CAM041457  38799  CAM041457_d.CR2   dorsal   
28286  CAM036145  41369  CAM036145_v.JPG  ventral   
21858  CAM017409  19047  CAM017409_d.CR2   dorsal   
12708  CAM010412  26792  CAM010412_v.CR2  ventral   

                                             zenodo_name  \
34925                               0.gmk.broods.all.csv   
28286                                       Filelist.csv   
21858  CAM.coll.PS.list.individuals.haplotagging.new....   
12708                          2001_2.broods.batch.1.csv   

                             zenodo_link Sequence  \
34925  https://zenodo.org/record/4291095   41,457   
28286  https://zenodo.org/record/5561246   36,145   
21858  https://zenodo.org/record/4153502   17,409   
12708  https://zenodo.org/record/2549524   10,412   

                        Taxonomic_Name                           Locality  \
34925              Heliconius timareta                  Reventador road 2   
28286               Methona singularis                    Guaribas - RG16   
21858  Heliconius erato ssp. lativitta  San Pedro de Arajuno, Río Arajuno   
12708                   Heliconius sp.                                NaN   

      Sample_accession  ... Cross_Type Stage      Sex Unit_Type file_type  \
34925              NaN  ...        NaN   NaN     Male       NaN       raw   
28286              NaN  ...        NaN   NaN     Male       NaN       jpg   
21858        ERS353373  ...        NaN   NaN   Female      wild       raw   
12708              NaN  ...        NaN   NaN  Unknown    reared       raw   

      record_number              species subspecies       genus  \
34925       4291095  Heliconius timareta        NaN  Heliconius   
28286       5561246   Methona singularis        NaN     Methona   
21858       4153502     Heliconius erato  lativitta  Heliconius   
12708       2549524       Heliconius sp.        NaN  Heliconius   

                                                file_url  
34925  https://zenodo.org/record/4291095/files/CAM041...  
28286  https://zenodo.org/record/5561246/files/CAM036...  
21858  https://zenodo.org/record/4153502/files/CAM017...  
12708  https://zenodo.org/record/2549524/files/CAM010...  

[4 rows x 27 columns]

### Add Proper Taxonomic Name for Crosstypes

We want the cross types to also have full taxonomic names (`Heliconius <species> <subspecies>`) so this can be used in downloading to appropriate branches and also for easier diversity counts. Cross Types will still be easily filtered using the `Cross_Type` column.

In [10]:
df.loc[df["Cross_Type"].notna(), "subspecies"].value_counts()

subspecies
(malleti x plesseni) x malleti                 1007
plesseni x (malleti x plesseni)                 462
(plesseni x malleti) x (malleti x plesseni)     348
(plesseni x malleti) x plesseni                 345
malleti x (plesseni x malleti)                  324
(plesseni x malleti) x (plesseni x malleti)     228
(malleti x plesseni) x plesseni                 216
plesseni x malleti                              212
malleti x plesseni                              156
lativitta x notabilis                           111
plesseni x (plesseni x malleti)                 106
(lativitta x notabilis) x notabilis              90
(lativitta x notabilis) x lativitta              90
(malleti x plesseni) x (malleti x plesseni)      81
(plesseni x malleti) x malleti                   80
(malleti x plesseni) x (plesseni x malleti)      42
malleti                                          28
plesseni                                         28
(latRo x notabilis) x notabilis                  12
l

In [11]:
df.loc[(df["Cross_Type"].notna()) & (df["subspecies"].isna()), "Cross_Type"].value_counts()

Cross_Type
Test cross (4 spots x 4 spots)                           150
Test cross (N heterozygocity - NBNN x malleti - thin)    114
Test cross (N heterozygozity)                             78
Test cross (short HW bar)                                 54
Test cross (4 spots x 2 banded)                           48
2 banded                                                  16
hybrid                                                    10
Ac heterozygote                                            4
Test cross (2 banded F2 x 2 banded F2)                     4
Name: count, dtype: int64

Notice that we have hybrids here which should be indicated as such though they don't all have an ` x ` in their name. We'll remember this for the `hybrid_stat` column and generate using the Cross Type indicator. Our only non-hybrid Cross Types are `malleti`, `plesseni`, and `lativitta`.

In [12]:
non_specific_cross_hybrids = df.loc[(df["Cross_Type"].notna()) & (df["subspecies"].isna()), "Cross_Type"].unique()
non_specific_cross_hybrids

array(['hybrid', 'Ac heterozygote', '2 banded',
       'Test cross (2 banded F2 x 2 banded F2)',
       'Test cross (4 spots x 2 banded)', 'Test cross (N heterozygozity)',
       'Test cross (short HW bar)', 'Test cross (4 spots x 4 spots)',
       'Test cross (N heterozygocity - NBNN x malleti - thin)'],
      dtype=object)

In [13]:
df.loc[df["Cross_Type"].isna(), "subspecies"].dropna().unique()

array(['cythera', 'cyrbia', 'venus', 'venus x chestertonii', 'vulcanus',
       'chestertonii', 'vulcanus x melpomene', 'lativitta', 'malleti',
       'erato', 'ssp.nov.P', 'melpomene', 'willmotti',
       'chestertonii x venus', 'eleuchia', 'cydnides', 'weymeri',
       'chioneus', 'demophoon', 'hydara', 'sapho', 'numata', 'iulia',
       'melpomene x thelxiope', 'wallacei', 'rosina', 'formosus',
       'melpomene x rosina', 'menapis', 'hydara x petiverana', 'decumana',
       'relata', 'agna', 'isthmia', 'bicoloratus', 'euphrasius',
       'salapia', 'matronalis', 'ethica', 'agnosia', 'andromica',
       'hippocrenis', 'saturata', 'evanides', 'lyra', 'pagasa',
       'staudingeri', 'valora', 'cassotis', 'chiriquensis', 'alithea',
       'timareta', 'plesseni', 'notabilis', 'amaryllis', 'thelxinoe',
       'doris', 'amaryllis x aglaope', 'aglaope', 'carbo', 'lycaste',
       'idae', 'macrinus', 'abida', 'notilla', 'neustetteri', 'giulia',
       'panamensis', 'eleusinus', 'agalla', 'x

In [14]:
def get_cross_taxa_name(species, cross_type):
    # label unspecified hybrids as such
    if cross_type in non_specific_cross_hybrids:
        return species + " " + "cross hybrid"
    
    # separate out hybrids from non-hybrids
    subsp_cross_list = cross_type.split("(")
    if len(subsp_cross_list) > 1:
        subsp_cross = subsp_cross_list[1].split(")")[0]
    else:
        subsp_cross = cross_type
    
    # Ensure order of hybrid names is consistent so they get placed in same folders (using scripts/download_jiggins.py)
    # And so counts by taxonomic name aren't needlessly skewed
    if subsp_cross == "malleti x plesseni":
        subsp_cross = "plesseni x malleti"
    elif subsp_cross == "lativitta x notabilis":
        subsp_cross = "notabilis x lativitta"
    
    # Set taxa_name as with non cross types labeled to subspecies
    taxa_name = species + " ssp. " + subsp_cross
    return taxa_name

In [15]:
for cross_type in list(df["Cross_Type"].dropna().unique()):
    print(get_cross_taxa_name("H.sp.", cross_type))

H.sp. ssp. malleti
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni
H.sp. ssp. plesseni x malleti
H.sp. ssp. latRo x notabilis
H.sp. ssp. latRo x notabilis
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni x malleti
H.sp. ssp. notabilis x lativitta
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni x malleti
H.sp. ssp. plesseni x malleti
H.sp. cross hybrid
H.sp. ssp. plesseni x malleti
H.sp. ssp. notabilis x lativitta
H.sp. ssp. notabilis x lativitta
H.sp. cross hybrid
H.sp. ssp. plesseni x malleti
H.sp. cross hybrid
H.sp. ssp. lativitta
H.sp. cross hybrid
H.sp. cross hybrid
H.sp. cross hybrid
H.sp. cross hybrid
H.sp. cross hybrid
H.sp. cross hybrid


In [16]:
df.loc[df["Cross_Type"].notna(), "species"].unique()

array(['Heliconius melpomene', 'Heliconius erato'], dtype=object)

In [17]:
# https://stackoverflow.com/a/52854800
df.loc[df["Cross_Type"].notna(), "Taxonomic_Name"] = df.loc[df["Cross_Type"].notna()].apply(lambda x: get_cross_taxa_name(x["species"], x["Cross_Type"]), axis = 1)
df.loc[df["Cross_Type"].notna(), "Taxonomic_Name"].unique()

array(['Heliconius melpomene ssp. malleti',
       'Heliconius melpomene ssp. plesseni x malleti',
       'Heliconius melpomene ssp. plesseni',
       'Heliconius erato ssp. latRo x notabilis',
       'Heliconius erato ssp. notabilis x lativitta',
       'Heliconius erato cross hybrid',
       'Heliconius melpomene cross hybrid',
       'Heliconius erato ssp. lativitta'], dtype=object)

In [18]:
df.Taxonomic_Name.nunique()

366

So we've added 3 more unique values of `Taxonomic_Name`, that checks out: `Heliconius erato ssp. latRo x notabilis`, `Heliconius erato cross hybrid`, and `Heliconius melpomene cross hybrid`.

### Add Hybrid Status Column

In [19]:
hybrids = [taxa_name for taxa_name in list(df["Taxonomic_Name"].dropna().unique()) if (" x " in taxa_name) or ("hybrid" in taxa_name)]
len(hybrids)

20

In [20]:
hybrids

['Heliconius erato ssp. venus x chestertonii',
 'Heliconius melpomene ssp. vulcanus x melpomene',
 'Heliconius erato ssp. chestertonii x venus',
 'Heliconius melpomene ssp. melpomene x thelxiope',
 'Heliconius melpomene ssp. melpomene x rosina',
 'Heliconius hybrid',
 'Heliconius erato ssp. hydara x petiverana',
 'Heliconius melpomene ssp. amaryllis x aglaope',
 'Anartia fatima x amathea',
 'Heliconius melpomene ssp. plesseni x malleti',
 'Heliconius erato ssp. notabilis x lativitta',
 'Heliconius erato ssp. latRo x notabilis',
 'Heliconius erato cross hybrid',
 'Heliconius melpomene cross hybrid',
 'Heliconius erato ssp. hydara x amalfreda',
 'Heliconius erato ssp. hydara x erato',
 'Heliconius melpomene ssp. meriana x melpomene',
 'Heliconius melpomene ssp. dignus x lativitta',
 'Heliconius melpomene ssp. malleti x bellula',
 'Heliconius melpomene ssp. malleti x vicina']

Observe that we have one species-level hybrid: `Anartia fatima x amathea`.

In [21]:
sp_hybrid_parents = ["Anartia fatima", "Anartia amathea"]

In [22]:
df["hybrid_stat"] = None
df.loc[df["subspecies"].notna(), "hybrid_stat"] = "non-hybrid"
df.loc[df["species"].isin(sp_hybrid_parents), "hybrid_stat"] = "non-hybrid"

df.loc[df["Taxonomic_Name"].isin(hybrids), "hybrid_stat"] = "hybrid"

In [23]:
df.loc[df["species"].isin(sp_hybrid_parents)]

CAMID      X       Image_name     View  \
7326  CAM002890   8482  CAM002890_v.JPG  ventral   
7327  CAM002890  45376  CAM002890_v.JPG  ventral   
7328  CAM002890  45375  CAM002890_d.JPG   dorsal   
7329  CAM002890   8481  CAM002890_d.JPG   dorsal   

                        zenodo_name                        zenodo_link  \
7326     CAM.coll.images.batch5.csv  https://zenodo.org/record/2684906   
7327  occurences_and_multimedia.csv  https://zenodo.org/record/3477891   
7328  occurences_and_multimedia.csv  https://zenodo.org/record/3477891   
7329     CAM.coll.images.batch5.csv  https://zenodo.org/record/2684906   

     Sequence  Taxonomic_Name   Locality Sample_accession  ... Stage     Sex  \
7326    2,890  Anartia fatima  El Tirao,              NaN  ...   NaN  Female   
7327    2,890  Anartia fatima  El Tirao,              NaN  ...   NaN  Female   
7328    2,890  Anartia fatima  El Tirao,              NaN  ...   NaN  Female   
7329    2,890  Anartia fatima  El Tirao,              NaN  ...   NaN  Female   

     Unit_Type file_type record_number         species subspecies    genus  \
7326      wild       jpg       2684906  Anartia fatima        NaN  Anartia   
7327      wild       jpg       3477891  Anartia fatima        NaN  Anartia   
7328      wild       jpg       3477891  Anartia fatima        NaN  Anartia   
7329      wild       jpg       2684906  Anartia fatima        NaN  Anartia   

                                               file_url hybrid_stat  
7326  https://zenodo.org/record/2684906/files/CAM002...  non-hybrid  
7327  https://zenodo.org/record/3477891/files/CAM002...  non-hybrid  
7328  https://zenodo.org/record/3477891/files/CAM002...  non-hybrid  
7329  https://zenodo.org/record/2684906/files/CAM002...  non-hybrid  

[4 rows x 28 columns]

In [24]:
df.loc[df["species"].str.lower() == "amathea"] #not represented in the dataset

Empty DataFrame
Columns: [CAMID, X, Image_name, View, zenodo_name, zenodo_link, Sequence, Taxonomic_Name, Locality, Sample_accession, Collected_by, Other_ID, Date, Dataset, Store, Brood, Death_Date, Cross_Type, Stage, Sex, Unit_Type, file_type, record_number, species, subspecies, genus, file_url, hybrid_stat]
Index: []

[0 rows x 28 columns]

In [25]:
df.loc[df["genus"] == "Anartia", "Taxonomic_Name"].value_counts()

Taxonomic_Name
Anartia fatima x amathea    60
Anartia fatima               4
Name: count, dtype: int64

In [26]:
df.sample(7)

CAMID      X         Image_name              View  \
40498  CAM043842  32098  CAM043842_hwv.JPG  hindwing ventral   
9192   CAM008567  46249    CAM008567_v.JPG           ventral   
14127  CAM010971  27577    CAM010971_d.CR2            dorsal   
5315   CAM000537   6676    CAM000537_d.JPG            dorsal   
585      19N0204  19553      19N0204_d.JPG            dorsal   
38875  CAM043366  30469    CAM043366_v.CR2           ventral   
19226  CAM016687  18917    CAM016687_d.CR2            dorsal   

                                             zenodo_name  \
40498                 batch2.Peru.image.names.Zenodo.csv   
9192                       occurences_and_multimedia.csv   
14127                          2001_2.broods.batch.1.csv   
5315                          CAM.coll.images.batch3.csv   
585                   0.sheffield.ps.nn.ikiam.batch1.csv   
38875                 batch1.Peru.image.names.Zenodo.csv   
19226  CAM.coll.PS.list.individuals.haplotagging.new....   

                             zenodo_link Sequence  \
40498  https://zenodo.org/record/4287444   43,842   
9192   https://zenodo.org/record/3477891    8,567   
14127  https://zenodo.org/record/2549524   10,971   
5315   https://zenodo.org/record/2682458      537   
585    https://zenodo.org/record/4288311      204   
38875  https://zenodo.org/record/3569598   43,366   
19226  https://zenodo.org/record/4153502   16,687   

                           Taxonomic_Name  \
40498              Catoblepia berecynthia   
9192                   Heliconius demeter   
14127                      Heliconius sp.   
5315     Heliconius melpomene ssp. rosina   
585       Heliconius erato ssp. lativitta   
38875                      Eunica pusilla   
19226  Heliconius melpomene ssp. plesseni   

                                                Locality Sample_accession  \
40498                                            B1prim3              NaN   
9192   Tarapoto-Yurimaguas (Km15), Tunel Cumbre, Fond...              NaN   
14127                                                NaN              NaN   
5315                                  Pipeline road 4km,              NaN   
585                                    Ikiam Mariposario              NaN   
38875                                             B6rec3              NaN   
19226                        El Topo, Baños - Puyo road,       SRS7540355   

       ... Stage   Sex Unit_Type file_type record_number  \
40498  ...   NaN   NaN       NaN       jpg       4287444   
9192   ...   NaN  Male      wild       jpg       3477891   
14127  ...   NaN  Male    reared       raw       2549524   
5315   ...   NaN  Male      wild       jpg       2682458   
585    ...   NaN  Male    reared       jpg       4288311   
38875  ...   NaN   NaN       NaN       raw       3569598   
19226  ...   NaN  Male      wild       raw       4153502   

                      species subspecies       genus  \
40498  Catoblepia berecynthia        NaN  Catoblepia   
9192       Heliconius demeter        NaN  Heliconius   
14127          Heliconius sp.        NaN  Heliconius   
5315     Heliconius melpomene     rosina  Heliconius   
585          Heliconius erato  lativitta  Heliconius   
38875          Eunica pusilla        NaN      Eunica   
19226    Heliconius melpomene   plesseni  Heliconius   

                                                file_url hybrid_stat  
40498  https://zenodo.org/record/4287444/files/CAM043...        None  
9192   https://zenodo.org/record/3477891/files/CAM008...        None  
14127  https://zenodo.org/record/2549524/files/CAM010...        None  
5315   https://zenodo.org/record/2682458/files/CAM000...  non-hybrid  
585    https://zenodo.org/record/4288311/files/19N020...  non-hybrid  
38875  https://zenodo.org/record/3569598/files/CAM043...        None  
19226  https://zenodo.org/record/4153502/files/CAM016...  non-hybrid  

[7 rows x 28 columns]

## Investigate entries with no Taxonomic Information

In [27]:
df.loc[df.Taxonomic_Name.isna()].info()

<class 'pandas.core.frame.DataFrame'>
Index: 3886 entries, 0 to 49350
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             3886 non-null   object
 1   X                 3886 non-null   int64 
 2   Image_name        3886 non-null   object
 3   View              3594 non-null   object
 4   zenodo_name       3886 non-null   object
 5   zenodo_link       3886 non-null   object
 6   Sequence          2951 non-null   object
 7   Taxonomic_Name    0 non-null      object
 8   Locality          70 non-null     object
 9   Sample_accession  24 non-null     object
 10  Collected_by      0 non-null      object
 11  Other_ID          30 non-null     object
 12  Date              70 non-null     object
 13  Dataset           461 non-null    object
 14  Store             345 non-null    object
 15  Brood             5 non-null      object
 16  Death_Date        2 non-null      object
 17  Cross_Type        

Wow, there are a surprising number of images with no taxonomic information.

In [28]:
no_taxa_cams = list(df.loc[df["Taxonomic_Name"].isna(), "CAMID"].unique())
no_taxa_entries = list(df.loc[df["Taxonomic_Name"].isna(), "X"])

no_taxa_cam_match = [camid for camid in list(df.loc[~df["X"].isin(no_taxa_entries), "CAMID"]) if camid in no_taxa_cams]
len(no_taxa_cam_match)

0

There are no CAMIDs that these can match to for taxonomic info recovery. Last option is to check the records they come from, then we'll remove them.

In [29]:
print(df.loc[df["X"].isin(no_taxa_entries), "record_number"].nunique())
df.loc[df["X"].isin(no_taxa_entries), "zenodo_link"].value_counts()[:5]

21


zenodo_link
https://zenodo.org/record/5526257    1324
https://zenodo.org/record/2554218     492
https://zenodo.org/record/4288311     486
https://zenodo.org/record/2555086     440
https://zenodo.org/record/5731587     388
Name: count, dtype: int64

These are across most of the records. We can check the one with the most, but otherwise they should likely be dropped (can save them in a separate CSV in case they are to be assessed at a later point).

The first appear to be all _Heliconius erato ssp. cyrbia_, so those could be realigned.

The second indicates all _Heliconius erato_.

The third is a mix, so not resolvable without an expert.

It seems record 2555086 is all bred specimens of _Heliconius erato demophoon_.

The fifth record is a mix, and not all are labeled in the excel file (in fact, there's a lot of red which is probably why they were excluded).

In [30]:
df.loc[df["record_number"] == 5526257, "Taxonomic_Name"].info()

<class 'pandas.core.series.Series'>
Index: 1324 entries, 45868 to 47191
Series name: Taxonomic_Name
Non-Null Count  Dtype 
--------------  ----- 
0 non-null      object
dtypes: object(1)
memory usage: 20.7+ KB


Ah, so these are all null, but all are of the same subspecies, so they can be labeled.

In [31]:
pot_single_taxa_records = []
for record_num in (df.loc[df["X"].isin(no_taxa_entries), "record_number"].unique()):
    temp = df.loc[df["record_number"] == record_num]
    if temp.loc[temp["Taxonomic_Name"].notna()].shape[0] == 0:
        pot_single_taxa_records.append(record_num)

len(pot_single_taxa_records)

4

In [32]:
pot_single_taxa_records

[5731587, 5526257, 2554218, 2555086]

In [33]:
df.loc[df.record_number.isin(pot_single_taxa_records)].sample(5)

CAMID      X       Image_name     View  \
46747  CAM045219  43439  CAM045219_d.JPG   dorsal   
47062  CAM045298  43756  CAM045298_v.CR2  ventral   
37255  CAM042050  43982  CAM042050_d.JPG   dorsal   
46992  CAM045281  43687  CAM045281_d.JPG   dorsal   
49106       F901  38167       F901_d.CR2   dorsal   

                             zenodo_name                        zenodo_link  \
46747  image.names.cook.island.erato.csv  https://zenodo.org/record/5526257   
47062  image.names.cook.island.erato.csv  https://zenodo.org/record/5526257   
37255          Collection_August2019.csv  https://zenodo.org/record/5731587   
46992  image.names.cook.island.erato.csv  https://zenodo.org/record/5526257   
49106         Anniina.Mattila.Bred.F.csv  https://zenodo.org/record/2555086   

      Sequence Taxonomic_Name Locality Sample_accession  ... Stage  Sex  \
46747   45,219            NaN      NaN              NaN  ...   NaN  NaN   
47062   45,298            NaN      NaN              NaN  ...   NaN  NaN   
37255   42,050            NaN      NaN              NaN  ...   NaN  NaN   
46992   45,281            NaN      NaN              NaN  ...   NaN  NaN   
49106      NaN            NaN      NaN              NaN  ...   NaN  NaN   

      Unit_Type file_type record_number species subspecies genus  \
46747       NaN       jpg       5526257     NaN        NaN   NaN   
47062       NaN       raw       5526257     NaN        NaN   NaN   
37255       NaN       jpg       5731587     NaN        NaN   NaN   
46992       NaN       jpg       5526257     NaN        NaN   NaN   
49106       NaN       raw       2555086     NaN        NaN   NaN   

                                                file_url hybrid_stat  
46747  https://zenodo.org/record/5526257/files/CAM045...        None  
47062  https://zenodo.org/record/5526257/files/CAM045...        None  
37255  https://zenodo.org/record/5731587/files/CAM042...        None  
46992  https://zenodo.org/record/5526257/files/CAM045...        None  
49106  https://zenodo.org/record/2555086/files/F901_d...        None  

[5 rows x 28 columns]

Christopher agrees that the following is sufficient to label images from the following three records:
>3 records seem to have all of just one indicated species/subspecies: https://zenodo.org/record/5526257, https://zenodo.org/record/2554218, and https://zenodo.org/record/2555086. According to their Zenodo pages, the first appear to be all _Heliconius erato ssp. cyrbia_, the second indicates all _Heliconius erato_, and the third it seems is all bred specimens of _Heliconius erato demophoon_. 

`Unit_Type` and some other details could potentially be realigned at a later date, but we'll stick with taxonomic information for now.

In [34]:
df.loc[df["record_number"] == 5526257, "Taxonomic_Name"] = "Heliconius erato ssp. cyrbia"
df.loc[df["record_number"] == 5526257, "genus"] = "Heliconius"
df.loc[df["record_number"] == 5526257, "species"] = "Heliconius erato"
df.loc[df["record_number"] == 5526257, "subspecies"] = "cyrbia"
df.loc[df["record_number"] == 5526257, "hybrid_stat"] = "non-hybrid"

In [35]:
df.loc[df["record_number"] == 2554218, "Taxonomic_Name"] = "Heliconius erato"
df.loc[df["record_number"] == 2554218, "genus"] = "Heliconius"
df.loc[df["record_number"] == 2554218, "species"] = "Heliconius erato"

In [36]:
df.loc[df["record_number"] == 2555086, "Taxonomic_Name"] = "Heliconius erato ssp. demophoon"
df.loc[df["record_number"] == 2555086, "genus"] = "Heliconius"
df.loc[df["record_number"] == 2555086, "species"] = "Heliconius erato"
df.loc[df["record_number"] == 2555086, "subspecies"] = "demophoon"
df.loc[df["record_number"] == 2555086, "hybrid_stat"] = "non-hybrid"

### Save record of entries with no Taxonomic Info

In [37]:
missing_taxa_df = df.loc[df.Taxonomic_Name.isna()]
missing_taxa_df.shape

(1630, 28)

In [39]:
missing_taxa_df.to_csv("../metadata/Missing_taxa_Jiggins_Zenodo_Master.csv", index = False)

### Drop Entries with no Taxonomic Information

In [40]:
master_df = df.loc[df.Taxonomic_Name.notna()]

## Final stats for all data in master file summarized here.

In [41]:
master_df.nunique()

CAMID               11991
X                   44809
Image_name          36281
View                    7
zenodo_name            33
zenodo_link            30
Sequence            10905
Taxonomic_Name        366
Locality              645
Sample_accession     1559
Collected_by           12
Other_ID             3081
Date                  807
Dataset                 8
Store                 137
Brood                 224
Death_Date             81
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          30
species               246
subspecies            155
genus                  94
file_url            44794
hybrid_stat             2
dtype: int64

In [42]:
master_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 44809 entries, 6 to 49358
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             44809 non-null  object
 1   X                 44809 non-null  int64 
 2   Image_name        44809 non-null  object
 3   View              44030 non-null  object
 4   zenodo_name       44809 non-null  object
 5   zenodo_link       44809 non-null  object
 6   Sequence          43877 non-null  object
 7   Taxonomic_Name    44809 non-null  object
 8   Locality          31708 non-null  object
 9   Sample_accession  4572 non-null   object
 10  Collected_by      3043 non-null   object
 11  Other_ID          14352 non-null  object
 12  Date              30730 non-null  object
 13  Dataset           37024 non-null  object
 14  Store             36220 non-null  object
 15  Brood             14258 non-null  object
 16  Death_Date        316 non-null    object
 17  Cross_Type       

### Update Master File with Hybrid Status and URL Columns (& unique records)

In [44]:
master_df.to_csv("../Jiggins_Zenodo_Img_Master.csv", index = False)

## Make Heliconius Subset

In [45]:
heliconius_subset = master_df.loc[master_df.genus.str.lower() == "heliconius"]

heliconius_subset.info()

<class 'pandas.core.frame.DataFrame'>
Index: 34265 entries, 6 to 49358
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             34265 non-null  object
 1   X                 34265 non-null  int64 
 2   Image_name        34265 non-null  object
 3   View              33486 non-null  object
 4   zenodo_name       34265 non-null  object
 5   zenodo_link       34265 non-null  object
 6   Sequence          33333 non-null  object
 7   Taxonomic_Name    34265 non-null  object
 8   Locality          21180 non-null  object
 9   Sample_accession  4572 non-null   object
 10  Collected_by      3043 non-null   object
 11  Other_ID          6404 non-null   object
 12  Date              20244 non-null  object
 13  Dataset           29926 non-null  object
 14  Store             26526 non-null  object
 15  Brood             14242 non-null  object
 16  Death_Date        316 non-null    object
 17  Cross_Type       

In [46]:
heliconius_subset.nunique()

CAMID               10109
X                   34265
Image_name          29192
View                    3
zenodo_name            33
zenodo_link            30
Sequence             9031
Taxonomic_Name        132
Locality              472
Sample_accession     1559
Collected_by           12
Other_ID             1865
Date                  776
Dataset                 8
Store                 121
Brood                 224
Death_Date             81
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          30
species                37
subspecies            110
genus                   1
file_url            34250
hybrid_stat             2
dtype: int64

In [47]:
heliconius_subset.View.value_counts()

View
dorsal                16882
ventral               16586
dorsal and ventral       18
Name: count, dtype: int64

Note that this subset is distributed across 30 Zenodo records from the [Butterfly Genetics Group](https://zenodo.org/communities/butterfly?q=&l=list&p=1&s=10&sort=newest).

### Save the Heliconius Subset to CSV


In [48]:
heliconius_subset.to_csv("../Jiggins_Heliconius_Master.csv", index = False)

## Make Dorsal Subset

In [49]:
dorsal_views = [view for view in list(master_df.View.dropna().unique()) if "dorsal" in view]

dorsal_subset = master_df.loc[master_df["View"].isin(dorsal_views)]
dorsal_subset.info()

<class 'pandas.core.frame.DataFrame'>
Index: 22175 entries, 7 to 49357
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             22175 non-null  object
 1   X                 22175 non-null  int64 
 2   Image_name        22175 non-null  object
 3   View              22175 non-null  object
 4   zenodo_name       22175 non-null  object
 5   zenodo_link       22175 non-null  object
 6   Sequence          21709 non-null  object
 7   Taxonomic_Name    22175 non-null  object
 8   Locality          15615 non-null  object
 9   Sample_accession  2294 non-null   object
 10  Collected_by      1533 non-null   object
 11  Other_ID          6916 non-null   object
 12  Date              15347 non-null  object
 13  Dataset           18250 non-null  object
 14  Store             18254 non-null  object
 15  Brood             6920 non-null   object
 16  Death_Date        106 non-null    object
 17  Cross_Type       

In [50]:
dorsal_subset.nunique()

CAMID               11776
X                   22175
Image_name          17907
View                    4
zenodo_name            33
zenodo_link            30
Sequence            10713
Taxonomic_Name        362
Locality              642
Sample_accession     1552
Collected_by           12
Other_ID             2890
Date                  791
Dataset                 8
Store                 137
Brood                 215
Death_Date             63
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          30
species               245
subspecies            152
genus                  94
file_url            22168
hybrid_stat             2
dtype: int64

Observe that we still have duplicate samples (duplicated `CAMID`), so we'll add a column indicating this (`CAM_Dupe`). We will not leave the first instance as a non-duplicate to have a clear assessment of all duplication (eg., is it just across a couple records).

Note that they will be duplicated for the images that are of a dorsal forewing or hindwing, so we will label those as `single_wing`.

In [51]:
dorsal_subset["CAM_Dupe"] = dorsal_subset.duplicated(subset = "CAMID", keep = False)
dorsal_subset.loc[dorsal_subset["View"].isin(["forewing dorsal", "hindwing dorsal"]), "CAM_Dupe"] = "single-wing"
dorsal_subset["CAM_Dupe"].value_counts()

/var/folders/nv/f0fq1p1n1_3b11x579py_0q80000gq/T/ipykernel_21745/2272441064.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dorsal_subset["CAM_Dupe"] = dorsal_subset.duplicated(subset = "CAMID", keep = False)


CAM_Dupe
True           17213
False           4170
single-wing      792
Name: count, dtype: int64

In [52]:
dorsal_subset.loc[dorsal_subset["CAM_Dupe"] == True, "record_number"].nunique()

29

Okay, nearly all records have duplication even in the dorsal subset. That does make sense when we have just over half as many unique `CAMID`s as number of images.

In [53]:
dorsal_subset.loc[dorsal_subset["CAM_Dupe"] == "single-wing", "record_number"].value_counts()

record_number
4287444    396
4288250    284
3569598    112
Name: count, dtype: int64

Single-wing images are constrained to 3 records.

In [54]:
dorsal_subset.loc[dorsal_subset["CAM_Dupe"] == True, "file_type"].value_counts()

file_type
jpg    11752
raw     5440
tif       21
Name: count, dtype: int64

Some of this duplication is by file type.

In [55]:
dorsal_subset.loc[(dorsal_subset["CAM_Dupe"] == True) & (dorsal_subset["file_type"] == "jpg")].duplicated(subset = "CAMID", keep = False).value_counts()

True     8415
False    3337
Name: count, dtype: int64

In [56]:
dorsal_subset.loc[(dorsal_subset["CAM_Dupe"] == True) & (dorsal_subset["file_type"] == "raw")].duplicated(subset = "CAMID", keep = False).value_counts()

False    4106
True     1334
Name: count, dtype: int64

We have multiple jpg images & multiple raw images of the same specimen. Note that this does not necessarily mean these are duplicates of the same images. There are also jpg copies provided alongside raw images.

### Save Dorsal Subset to CSV

In [57]:
dorsal_subset.to_csv("../Jiggins_Zenodo_dorsal_Img_Master.csv", index = False)